In this problem we need to simulate a simplified airport security system at a busy airport. Passengers arrive according to a Poisson distribution with λ1 = 5 per minute (i.e., mean interarrival rate 1 = 0.2 minutes) to the ID/boarding-pass check queue, where there are several servers who each have exponential service time with mean rate 2 = 0.75 minutes.After that, the passengers are assigned to the shortest of the several personal-check queues, where they go through the personal scanner (time is uniformly distributed between 0.5 minutes and 1 minute). 

We are going to use Python with SimPy to build a simulation of the system, and then vary the number of ID/boarding-pass checkers and personal-check queues to determine how many are needed to keep average wait times below 15 minutes.  


Import libraries

In [180]:
import simpy
import random

Define the rates

In [181]:
# Inter-arrival mean rate. Create a passeger every 0.2 minutes
interarrival_rate = 0.2
# Exponential check time mean rate. Minutes it takes to serve a passeger
check_rate = .75 
# Scanner min time - uniform distribution
min_scan = .5
# Scanner max time - uniform distribution
max_scan = 1.0 
# Rate of arrival per minute
arrival_rate = 5
# Minutes per simulation
run_time = 480 
# Number of simulation replications
reps = 20 
# Number of boarding pass checkers
num_checkers = 5
# Number of scanners
num_scanners = 50
# Random seed
random_seed = 123

Create a class to perform the simulation.
We need to create an airport simulation object with checkers and scanners.

In [182]:
class Airport(object):
    
    # The first thing is to initialize the class object using _init_ function.
    # We also need to define the resources in our simulation system (i.e. checkers and scanners).
    def __init__(self, env, num_checkers, num_scanners, check_rate, max_scan , min_scan):

        # Here we set up the simpy enviroment.
        self.env = env
        self.num_checkers = num_checkers
        self.num_scanners = num_scanners
        self.check_rate = check_rate
        self.max_scan = max_scan 
        self.min_scan = min_scan

        # We set up the checkers as a resource within our simulation system. 
        # We including 5 checks here as defined earlier using num_checkers.
        self.checker = simpy.Resource(env, self.num_checkers)

        # Set up scanners as a resource, note each scanner has it's own queue. So we need to manage it differently.
        self.scanners = []

        # We have 5 (defined as num_scanners) scanners, we need to assign a single resource to each scanner.
        for i in range(0,self.num_scanners):
            resource = simpy.Resource(env, capacity = 1)
            self.scanners.append(resource)
        
    # Let's define how long a singe passenger takes to checkout.
    def passagerCheck(self, passenger):
        yield self.env.timeout(random.expovariate(1/self.check_rate))

    # Lets define how long a single passenger takes to be scanned.
    def passagerScan(self, passenger):
        yield self.env.timeout(random.uniform(self.max_scan , self.min_scan))


Lets define variables to make use in our analysis and initialize them to zero.

In [183]:
check_wait = 0
scan_wait = 0
system_time = 0
time_wait = 0
time_checker = 0
time_checker_complete = 0
time_scan = 0
time_scan_complete = 0
passenger_count = 0
scan_time = 0
check_time = 0

Lets define a passenger.
When a passenger arrives and how the passenger move through the system.

In [184]:
def passenger(name, airport, env, p_count): # parameters : name, airport,enviroment, passenger count
    
    # Let's define global variables
    global check_wait
    global scan_wait
    global system_time
    global time_wait
    global time_checker
    global time_checker_complete
    global time_scan
    global time_scan_complete
    global passenger_count
    global scan_time
    global check_time

    # Let's capture the time passenger arrives.
    time_arrive = env.now
    print('%s arrives at time %.2f' % (name, time_arrive))

    with airport.checker.request() as request:
        yield request
        print('check queue length = %d' % len(airport.checker.queue))

        # Let's capture the time passenger arrives at checker
        time_checker = env.now
        print('%s gets to checker at time %.2f' % (name, time_checker))

        yield env.process(airport.passagerCheck(name))

        # Let's capture the time passenger completes checker
        time_checker_complete = env.now
        print('%s complete checking at time %.2f' % (name, time_checker_complete))

    # We check the scanning queue.
    min_q = 0

    with airport.scanners[min_q].request() as request:
        yield request
        print('scanner queue length = %d' % len(airport.scanners[min_q].queue))

        for i in range(1, num_scanners):
            #Add the passenger to the shortest queue
            if (len(airport.scanners[i].queue) < len(airport.scanners[min_q].queue)):
                min_q = i

        # The time a passenger arrives at a scanner.
        time_scan = env.now
        print('%s gets to a scanner at time %.2f' % (name, time_scan))

        yield env.process(airport.passagerScan(name))
        
         # The time a passenger completes at a scanner.
        time_scan_complete = env.now
        print('%s complete scanning at time %.2f' % (name, time_scan_complete))

    
    # The time a passenger completes the entire process
    time_exit = env.now
    print('%s gets to complete system process at time %.2f' % (name, time_exit))

    # Below is record of all passengers that completed the process.
    
    # Time it takes to complete the process
    system_time = system_time + (time_exit - time_arrive)
    # The wait period before the passeger is checked.
    check_wait = check_wait + (time_checker - time_arrive)
    # The check time.
    check_time = check_time + (time_checker_complete - time_checker) 
    # The wait between when a passenger entering the scanning queue and completing scanning
    scan_wait = scan_wait + (time_scan - time_checker_complete)
    # The scan time.
    scan_time = scan_time + (time_scan_complete - time_scan)
    # Total wait per passenger.
    time_wait = (check_wait + scan_wait)
    # Track the passenger count.
    passenger_count = p_count

We setup the environment.

In [185]:
def setup(env, num_checkers, num_scanners, check_rate, max_scan , min_scan):
    
    
    # Create the Airport
    airport = Airport(env,num_checkers, num_scanners, check_rate, max_scan , min_scan)

    passengerCount = 0
    # Create more passengers while the simulation is running
    while True:
        yield env.timeout(random.expovariate(1.0 / check_rate))
        passengerCount += 1
        env.process(passenger('Passenger %d' % passengerCount, airport, env, passengerCount))

Lets define the variables to store simulation results into and start the simulation process.

In [186]:
# Define lists to help in our analysis.
mean_wait_time = []
mean_check_time = []
mean_scan_time = []
mean_system_time = []
mean_scan_wait_time = []
mean_check_wait_time = []



for i in range(0, reps):
    
    # Create simpy environment
    env = simpy.Environment()
    env.process(setup(env, num_checkers, num_scanners, check_rate, max_scan , min_scan))
    env.run(until = run_time)
    
    #Find mean of our system parameters     
    mean_wait_time.append(time_wait/passenger_count)
    mean_check_time.append(check_time/passenger_count)
    mean_scan_time.append(scan_time/passenger_count)
    mean_system_time.append(system_time/passenger_count)
    mean_scan_wait_time.append(scan_wait/passenger_count)
    mean_check_wait_time.append(check_wait/passenger_count)


    # Reset the parameter
    system_time = 0
    check_wait = 0
    scan_wait = 0
    time_wait = 0
    scan_wait_time = 0
    check_wait_time = 0

Passenger 1 arrives at time 0.87
check queue length = 0
Passenger 1 gets to checker at time 0.87
Passenger 2 arrives at time 1.03
check queue length = 0
Passenger 2 gets to checker at time 1.03
Passenger 1 complete checking at time 1.13
scanner queue length = 0
Passenger 1 gets to a scanner at time 1.13
Passenger 2 complete checking at time 1.70
Passenger 1 complete scanning at time 2.09
Passenger 1 gets to complete system process at time 2.09
scanner queue length = 0
Passenger 2 gets to a scanner at time 2.09
Passenger 3 arrives at time 2.33
check queue length = 0
Passenger 3 gets to checker at time 2.33
Passenger 2 complete scanning at time 2.72
Passenger 2 gets to complete system process at time 2.72
Passenger 3 complete checking at time 2.92
scanner queue length = 0
Passenger 3 gets to a scanner at time 2.92
Passenger 4 arrives at time 2.94
check queue length = 0
Passenger 4 gets to checker at time 2.94
Passenger 4 complete checking at time 3.28
Passenger 5 arrives at time 3.36
che

Passenger 439 gets to a scanner at time 351.07
Passenger 444 arrives at time 351.61
check queue length = 0
Passenger 444 gets to checker at time 351.61
Passenger 439 complete scanning at time 351.88
Passenger 439 gets to complete system process at time 351.88
scanner queue length = 1
Passenger 440 gets to a scanner at time 351.88
Passenger 442 complete checking at time 351.92
Passenger 443 complete checking at time 352.45
Passenger 444 complete checking at time 352.68
Passenger 440 complete scanning at time 352.79
Passenger 440 gets to complete system process at time 352.79
scanner queue length = 3
Passenger 441 gets to a scanner at time 352.79
Passenger 445 arrives at time 353.41
check queue length = 0
Passenger 445 gets to checker at time 353.41
Passenger 441 complete scanning at time 353.61
Passenger 441 gets to complete system process at time 353.61
scanner queue length = 2
Passenger 442 gets to a scanner at time 353.61
Passenger 446 arrives at time 353.72
check queue length = 0
Pa

Passenger 168 arrives at time 126.28
check queue length = 0
Passenger 168 gets to checker at time 126.28
Passenger 166 complete scanning at time 126.42
Passenger 166 gets to complete system process at time 126.42
scanner queue length = 0
Passenger 167 gets to a scanner at time 126.42
Passenger 168 complete checking at time 126.69
Passenger 169 arrives at time 127.28
check queue length = 0
Passenger 169 gets to checker at time 127.28
Passenger 167 complete scanning at time 127.34
Passenger 167 gets to complete system process at time 127.34
scanner queue length = 0
Passenger 168 gets to a scanner at time 127.34
Passenger 170 arrives at time 127.76
check queue length = 0
Passenger 170 gets to checker at time 127.76
Passenger 171 arrives at time 128.04
check queue length = 0
Passenger 171 gets to checker at time 128.04
Passenger 171 complete checking at time 128.06
Passenger 168 complete scanning at time 128.21
Passenger 168 gets to complete system process at time 128.21
scanner queue leng

Passenger 619 arrives at time 448.46
check queue length = 0
Passenger 619 gets to checker at time 448.46
Passenger 618 complete checking at time 449.00
Passenger 620 arrives at time 449.08
check queue length = 0
Passenger 620 gets to checker at time 449.08
Passenger 619 complete checking at time 449.08
Passenger 590 complete scanning at time 449.41
Passenger 590 gets to complete system process at time 449.41
scanner queue length = 28
Passenger 591 gets to a scanner at time 449.41
Passenger 621 arrives at time 449.71
check queue length = 0
Passenger 621 gets to checker at time 449.71
Passenger 621 complete checking at time 449.82
Passenger 620 complete checking at time 450.31
Passenger 591 complete scanning at time 450.32
Passenger 591 gets to complete system process at time 450.32
scanner queue length = 29
Passenger 592 gets to a scanner at time 450.32
Passenger 592 complete scanning at time 450.88
Passenger 592 gets to complete system process at time 450.88
scanner queue length = 28
P

Passenger 381 gets to complete system process at time 293.75
scanner queue length = 33
Passenger 379 gets to a scanner at time 293.75
Passenger 414 complete checking at time 293.88
Passenger 417 complete checking at time 294.29
Passenger 416 complete checking at time 294.39
Passenger 379 complete scanning at time 294.43
Passenger 379 gets to complete system process at time 294.43
scanner queue length = 35
Passenger 384 gets to a scanner at time 294.43
Passenger 384 complete scanning at time 294.99
Passenger 384 gets to complete system process at time 294.99
scanner queue length = 34
Passenger 383 gets to a scanner at time 294.99
Passenger 383 complete scanning at time 295.54
Passenger 383 gets to complete system process at time 295.54
scanner queue length = 33
Passenger 382 gets to a scanner at time 295.54
Passenger 382 complete scanning at time 296.41
Passenger 382 gets to complete system process at time 296.41
scanner queue length = 32
Passenger 385 gets to a scanner at time 296.41
P

...

Passenger 560 arrives at time 462.45
check queue length = 0
Passenger 560 gets to checker at time 462.45
Passenger 560 complete checking at time 462.58
scanner queue length = 0
Passenger 560 gets to a scanner at time 462.58
Passenger 560 complete scanning at time 463.25
Passenger 560 gets to complete system process at time 463.25
Passenger 561 arrives at time 463.37
check queue length = 0
Passenger 561 gets to checker at time 463.37
Passenger 562 arrives at time 463.71
check queue length = 0
Passenger 562 gets to checker at time 463.71
Passenger 561 complete checking at time 464.17
scanner queue length = 0
Passenger 561 gets to a scanner at time 464.17
Passenger 563 arrives at time 464.28
check queue length = 0
Passenger 563 gets to checker at time 464.28
Passenger 563 complete checking at time 464.30
Passenger 561 complete scanning at time 464.90
Passenger 561 gets to complete system process at time 464.90
scanner queue length = 0
Passenger 563 gets to a scanner at time 464.90
Passeng

check queue length = 0
Passenger 411 gets to checker at time 324.21
Passenger 412 arrives at time 324.27
check queue length = 0
Passenger 412 gets to checker at time 324.27
Passenger 411 complete checking at time 324.31
Passenger 399 complete scanning at time 324.80
Passenger 399 gets to complete system process at time 324.80
scanner queue length = 10
Passenger 400 gets to a scanner at time 324.80
Passenger 412 complete checking at time 325.06
Passenger 400 complete scanning at time 325.52
Passenger 400 gets to complete system process at time 325.52
scanner queue length = 10
Passenger 401 gets to a scanner at time 325.52
Passenger 401 complete scanning at time 326.05
Passenger 401 gets to complete system process at time 326.05
scanner queue length = 9
Passenger 402 gets to a scanner at time 326.05
Passenger 402 complete scanning at time 326.88
Passenger 402 gets to complete system process at time 326.88
scanner queue length = 8
Passenger 404 gets to a scanner at time 326.88
Passenger 4

Passenger 226 complete checking at time 171.86
Passenger 215 complete scanning at time 171.97
Passenger 215 gets to complete system process at time 171.97
scanner queue length = 10
Passenger 217 gets to a scanner at time 171.97
Passenger 217 complete scanning at time 172.96
Passenger 217 gets to complete system process at time 172.96
scanner queue length = 9
Passenger 218 gets to a scanner at time 172.96
Passenger 227 complete checking at time 173.21
Passenger 218 complete scanning at time 173.80
Passenger 218 gets to complete system process at time 173.80
scanner queue length = 9
Passenger 219 gets to a scanner at time 173.80
Passenger 219 complete scanning at time 174.78
Passenger 219 gets to complete system process at time 174.78
scanner queue length = 8
Passenger 216 gets to a scanner at time 174.78
Passenger 216 complete scanning at time 175.51
Passenger 216 gets to complete system process at time 175.51
scanner queue length = 7
Passenger 220 gets to a scanner at time 175.51
Passe

Passenger 36 complete scanning at time 29.00
Passenger 36 gets to complete system process at time 29.00
scanner queue length = 4
Passenger 37 gets to a scanner at time 29.00
Passenger 43 arrives at time 29.23
check queue length = 0
Passenger 43 gets to checker at time 29.23
Passenger 44 arrives at time 29.63
check queue length = 0
Passenger 44 gets to checker at time 29.63
Passenger 45 arrives at time 29.65
check queue length = 0
Passenger 45 gets to checker at time 29.65
Passenger 37 complete scanning at time 29.68
Passenger 37 gets to complete system process at time 29.68
scanner queue length = 3
Passenger 34 gets to a scanner at time 29.68
Passenger 44 complete checking at time 29.69
Passenger 42 complete checking at time 29.70
Passenger 46 arrives at time 29.72
check queue length = 0
Passenger 46 gets to checker at time 29.72
Passenger 47 arrives at time 29.86
check queue length = 0
Passenger 47 gets to checker at time 29.86
Passenger 47 complete checking at time 29.88
Passenger 43

Passenger 438 complete checking at time 328.22
Passenger 436 complete scanning at time 328.23
Passenger 436 gets to complete system process at time 328.23
scanner queue length = 3
Passenger 435 gets to a scanner at time 328.23
Passenger 439 arrives at time 328.29
check queue length = 0
Passenger 439 gets to checker at time 328.29
Passenger 435 complete scanning at time 329.19
Passenger 435 gets to complete system process at time 329.19
scanner queue length = 2
Passenger 434 gets to a scanner at time 329.19
Passenger 440 arrives at time 329.72
check queue length = 0
Passenger 440 gets to checker at time 329.72
Passenger 441 arrives at time 329.93
check queue length = 0
Passenger 441 gets to checker at time 329.93
Passenger 439 complete checking at time 330.00
Passenger 434 complete scanning at time 330.07
Passenger 434 gets to complete system process at time 330.07
scanner queue length = 2
Passenger 437 gets to a scanner at time 330.07
Passenger 442 arrives at time 330.18
check queue le

Perform the analysis. We had 20 replications,whe recorded the simulation parameters in four lists:  
mean_wait_time, mean_check_time, mean_scan_time and mean_sys_time.

In [187]:
simulation_cumulative_waitiing_average = sum(mean_wait_time) / reps
simulation_cumulative_checking_average = sum(mean_check_time) / reps
simulation_cumulative_scanning_average = sum(mean_scan_time) / reps
simulation_cumulative_system_processing_time = sum(mean_system_time) / reps
simulation_cumulative_scan_wait_average = sum(mean_scan_wait_time) / reps
simulation_cumulative_system_check_wait_average = sum(mean_check_wait_time) / reps


print('Cumulative waiting average time: ' + str(simulation_cumulative_waitiing_average))
print('Cumulative checking average time: ' + str(simulation_cumulative_checking_average))
print('Cumulative scanning average time: ' + str(simulation_cumulative_scanning_average))
print('Cumulative check wait average time: ' + str(simulation_cumulative_system_check_wait_average))
print('Cumulative scan wait average time: ' + str(abs(simulation_cumulative_scan_wait_average)))
print('Average Cumulative system process time (overrall): ' + str(simulation_cumulative_system_processing_time))
print('Total number of passengers served : '+ str(passenger_count))

Cumulative waiting average time: 8.946658494575468
Cumulative checking average time: 0.10082590504411156
Cumulative scanning average time: 8.008101103610873
Cumulative check wait average time: 8.954405720334563
Cumulative scan wait average time: 0.0077472257590981575
Average Cumulative system process time (overrall): 9.708155816116616
Total number of passengers served : 607
